# 1. Préparation des données

In [1]:
import pandas as pd 
import numpy as np 
import tensorflow as tf 
import tensorflow_hub as hub 
from transformers import BertTokenizer, BertModel 
import torch 
from transformers import GPT2Tokenizer, GPT2Model 

In [2]:
documents = [ 
    "Je suis heureux d'être ici.", 
    "L'apprentissage automatique est fascinant.", 
    "Les modèles de langage sont importants pour le NLP.", 
    "Le NLP se concentre sur le traitement du langage naturel.", 
    "Les embeddings de mots capturent le sens des mots." 
] 

# 2. Implémentation des techniques contextualisé

## A.ELMO

In [3]:
# I'm going to retain the stopwords and the punctuation since ElMo can associate meaning to them
from nltk.corpus import stopwords
import string

def preprocess(doc):
    doc = doc.lower()
    return doc

preprocessed_docs = [preprocess(doc) for doc in documents]

In [ ]:
# Ce code est nécessaire pour pouvoir réexécuter la cellule au-dessous,il concisite à supprimer le modèle ELMO téléchargé uaparavant pour pouvoir le rétélecharger et en outre réexécuter dans ce notebook
import shutil

# Chemin du dossier temporaire TensorFlow Hub
temp_tfhub_path = r"C:\Users\Admin\AppData\Local\Temp\tfhub_modules"

# Supprimer le dossier
shutil.rmtree(temp_tfhub_path, ignore_errors=True)

In [6]:
#import os
#os.environ["TFHUB_DOWNLOAD_TIMEOUT"] = "300"

elmo = hub.load("https://tfhub.dev/google/elmo/3") 

def elmo_vectors(preprocessed_docs): 
    embeddings = elmo.signatures['default'](tf.constant(documents))['elmo'] 
    return embeddings

In [7]:
# Extraction des embeddings 
elmo_embeddings = elmo_vectors(preprocessed_docs) 
print(elmo_embeddings) 

tf.Tensor(
[[[-1.4885306  -0.41149336 -0.24441382 ... -0.41426605 -0.06543982
    0.05183329]
  [-1.3027904   0.07226025  0.29943648 ... -0.22295287  0.54361784
   -0.23196852]
  [-1.0080048  -0.40043336  0.72564054 ... -0.31716952  0.5674282
   -0.26984447]
  ...
  [-0.0284084  -0.04353216  0.04130161 ...  0.02583168 -0.01429836
   -0.01650423]
  [-0.0284084  -0.04353216  0.04130161 ...  0.02583168 -0.01429836
   -0.01650423]
  [-0.0284084  -0.04353216  0.04130161 ...  0.02583168 -0.01429836
   -0.01650423]]

 [[-0.44526702 -0.5597842   0.03786941 ...  0.16168292 -0.21517798
   -0.75935525]
  [-0.35717845  0.08124118  0.3269438  ...  0.02485686  0.51458216
    0.06116124]
  [-0.7284575   0.05236634  0.49155295 ... -0.03904716  0.66243196
    0.22367269]
  ...
  [-0.0284084  -0.04353216  0.04130161 ...  0.02583168 -0.01429836
   -0.01650423]
  [-0.0284084  -0.04353216  0.04130161 ...  0.02583168 -0.01429836
   -0.01650423]
  [-0.0284084  -0.04353216  0.04130161 ...  0.02583168 -0.01429

L'output de ELMo est un tenseur de forme `(5, 10, 1024)`, représentant 5 phrases, chacune avec un maximum de 10 tokens, et chaque token étant encodé par un vecteur de 1024 dimensions. Les valeurs reflètent des représentations contextuelles des mots, adaptées à leur contexte dans la phrase. Les vecteurs des tokens de padding (e.g., `[-0.0284084, -0.04353216, ...]`) doivent être ignorés. Pour utiliser ces embeddings, on peut moyenner les vecteurs de chaque phrase pour obtenir une représentation unique par phrase.

La différence clé est que les embeddings ELMo sont contextuels : ils varient selon le contexte de chaque mot dans une phrase. En revanche, les embeddings de Word2Vec sont statiques : un mot a toujours le même vecteur, quel que soit son contexte. Par exemple, "banc" dans "banc de poissons" et "banc de parc" aura un vecteur différent avec ELMo, mais identique avec Word2Vec.

## B. Bert

In [8]:
# Charger le tokenizer et le modèle BERT 
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased') 
model = BertModel.from_pretrained('bert-base-uncased') 

A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

In [9]:
# Préparation des données 
inputs = tokenizer(preprocessed_docs, return_tensors="pt", padding=True, truncation=True) 
 
# Calcul des embeddings 
with torch.no_grad(): 
    outputs = model(**inputs) 
embeddings = outputs.last_hidden_state 
print("Embedding BERT pour chaque mot dans le premier document:", embeddings[0]) 

Embedding BERT pour chaque mot dans le premier document: tensor([[-0.3921,  0.0615, -0.2947,  ..., -0.3531,  0.1835,  0.6495],
        [-0.2415,  0.4532, -0.2194,  ..., -0.3217,  0.4901,  0.2634],
        [-0.2805,  0.2195,  0.1591,  ..., -0.5845, -0.0106, -0.0433],
        ...,
        [-0.2133,  0.6835,  0.2230,  ..., -0.3057,  0.0222,  0.5110],
        [ 0.2331,  0.8774,  0.2998,  ..., -0.5109, -0.0103,  0.2446],
        [-0.2562,  0.3744,  0.1993,  ..., -0.1660,  0.0495,  0.4405]])


BERT génère des embeddings contextuels, où chaque mot est représenté par un vecteur prenant en compte son contexte dans la phrase. Cela est rendu possible grâce à son architecture basée sur les Transformers, qui utilise des mécanismes d'attention pour modéliser les relations entre tous les mots de la séquence, indépendamment de leur position.

Cette capacité à capturer le contexte rend BERT particulièrement efficace pour les tâches nécessitant une compréhension fine du langage. Dans ces tâches, il peut identifier non seulement les mots clés, mais aussi les relations contextuelles complexes entre la question et le texte source, améliorant ainsi la pertinence et l'exactitude des réponses fournies. BERT surpasse ainsi les modèles statiques comme Word2Vec, qui ne tiennent pas compte du contexte des mots.

# 4. Extension du Corpus avec NLTK et Analyse des Temps d'Exécution 

In [10]:
import nltk
nltk.download('movie_reviews') 
from nltk.corpus import movie_reviews 
# Charger les phrases du corpus 
corpus = [" ".join(movie_reviews.words(fileid)) for fileid in movie_reviews.fileids()] 

[nltk_data] Downloading package movie_reviews to
[nltk_data]     C:\Users\Admin\AppData\Roaming\nltk_data...
[nltk_data]   Package movie_reviews is already up-to-date!


In [ ]:
from nltk.tokenize import word_tokenize

stop_words = set(stopwords.words('english'))
punctuation = set(string.punctuation)


def preprocess_text(text):
    tokens = word_tokenize(text.lower())
    # Suppression des stop words et de la ponctuation
    cleaned_tokens = [word for word in tokens if word not in stop_words and word not in punctuation]
    return cleaned_tokens

# Application du pré-traitement au corpus
preprocessed_corpus = [preprocess_text(doc) for doc in corpus]

print("Texte original :", corpus[0][:200], "\n")
print("Texte pré-traité :", preprocessed_corpus[0][:20])

Texte original : plot : two teen couples go to a church party , drink and then drive . they get into an accident . one of the guys dies , but his girlfriend continues to see him in her life , and has nightmares . what 

Texte pré-traité : ['plot', 'two', 'teen', 'couples', 'go', 'church', 'party', 'drink', 'drive', 'get', 'accident', 'one', 'guys', 'dies', 'girlfriend', 'continues', 'see', 'life', 'nightmares', 'deal']


In [ ]:
elmo_embeddings = elmo_vectors(preprocessed_corpus)

In [14]:
elmo_embeddings

<tf.Tensor: shape=(5, 10, 1024), dtype=float32, numpy=
array([[[-1.4885306 , -0.41149336, -0.24441382, ..., -0.41426605,
         -0.06543982,  0.05183329],
        [-1.3027904 ,  0.07226025,  0.29943648, ..., -0.22295287,
          0.54361784, -0.23196852],
        [-1.0080048 , -0.40043336,  0.72564054, ..., -0.31716952,
          0.5674282 , -0.26984447],
        ...,
        [-0.0284084 , -0.04353216,  0.04130161, ...,  0.02583168,
         -0.01429836, -0.01650423],
        [-0.0284084 , -0.04353216,  0.04130161, ...,  0.02583168,
         -0.01429836, -0.01650423],
        [-0.0284084 , -0.04353216,  0.04130161, ...,  0.02583168,
         -0.01429836, -0.01650423]],

       [[-0.44526702, -0.5597842 ,  0.03786941, ...,  0.16168292,
         -0.21517798, -0.75935525],
        [-0.35717845,  0.08124118,  0.3269438 , ...,  0.02485686,
          0.51458216,  0.06116124],
        [-0.7284575 ,  0.05236634,  0.49155295, ..., -0.03904716,
          0.66243196,  0.22367269],
        ...,

In [16]:
print(f"Nombre de documents : {len(preprocessed_corpus)}")
print(f"Longueur moyenne (en tokens) : {sum(len(tokenizer(doc)['input_ids']) for doc in preprocessed_corpus) / len(preprocessed_corpus)}")

Nombre de documents : 2000
Longueur moyenne (en tokens) : 364.1545


In [18]:
# Vérifie si les embeddings ont déjà été calculés
if 'bert_embeddings' in globals():
    print("Embeddings déjà calculés. Réutilisation possible.")

Embeddings déjà calculés. Réutilisation possible.


In [22]:
# Définir le device (GPU si disponible, sinon CPU)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = model.to(device)  # Déplacer le modèle vers le device (GPU ou CPU)

# Initialiser la liste pour stocker les embeddings BERT
bert_embeddings = []

# Effectuer le traitement par lot sur les données d'entrée
batch_size = 16  # Vous pouvez ajuster en fonction de votre mémoire GPU/CPU
data_loader = torch.utils.data.DataLoader(
    list(zip(inputs['input_ids'], inputs['attention_mask'])),
    batch_size=batch_size
)

for batch in data_loader:
    input_ids, attention_mask = batch
    input_ids = input_ids.to(device)  # Déplacer vers le device
    attention_mask = attention_mask.to(device)  # Déplacer vers le device

    with torch.no_grad():
        # Appliquer BERT sur le batch
        outputs = model(input_ids=input_ids, attention_mask=attention_mask)

    # Extraire le vecteur moyen des états cachés (ou [CLS] token)
    # Option 1: Utiliser la moyenne sur tous les tokens du batch
    batch_embeddings = outputs.last_hidden_state.mean(dim=1).cpu().numpy()

    # Option 2: Utiliser uniquement le vecteur du token [CLS]
    # batch_embeddings = outputs.last_hidden_state[:, 0, :].cpu().numpy()

    # Ajouter les embeddings du batch à la liste
    bert_embeddings.extend(batch_embeddings)

print(f"Nombre d'embeddings générés : {len(bert_embeddings)}")

Nombre d'embeddings générés : 541


In [23]:
bert_embeddings

[array([-1.41008154e-01, -7.46946186e-02, -1.49860695e-01,  8.91784504e-02,
         3.67911421e-02,  6.57889172e-02,  1.26362652e-01, -1.45866320e-01,
        -8.63976330e-02, -5.01038320e-02, -2.19548687e-01,  2.00651929e-01,
        -5.10935532e-03,  2.27818832e-01, -8.28941911e-02, -8.18703696e-02,
        -1.11995734e-01, -9.30043012e-02,  1.78471934e-02,  3.03765256e-02,
         1.42390067e-02,  1.16459653e-01, -9.22324657e-02, -4.30680811e-01,
         1.37514517e-01,  3.82637024e-01, -4.07745034e-01, -2.64506340e-01,
        -1.29699960e-01,  6.10306442e-01, -1.28299594e-01,  1.44514656e-02,
         2.50836611e-01,  3.95204216e-01, -3.33237022e-01, -1.21837251e-01,
        -3.41398083e-02,  1.17322139e-01, -1.87771395e-01, -1.78722575e-01,
        -4.72080037e-02,  1.38311386e-01,  1.88341618e-01, -2.71901220e-01,
         1.91362709e-01,  2.15367585e-01,  4.86745909e-02, -1.48757011e-01,
        -2.72204489e-01, -3.13774079e-01, -9.76012349e-02,  7.23115578e-02,
        -5.6

# Recherche

## Roberta

In [ ]:
from transformers import RobertaTokenizer, RobertaModel

# Charger le tokenizer et le modèle RoBERTa
roberta_tokenizer = RobertaTokenizer.from_pretrained('roberta-base')
roberta_model = RobertaModel.from_pretrained('roberta-base')

# Encodage des documents
roberta_embeddings = []
for doc in preprocessed_corpus:
    inputs = roberta_tokenizer(doc, return_tensors='pt', padding=True, truncation=True, max_length=512)
    with torch.no_grad():
        outputs = roberta_model(**inputs)
    # Extraire l'embedding
    roberta_embeddings.append(outputs.last_hidden_state.mean(dim=1).squeeze().numpy())

## GPT

In [ ]:
from transformers import GPT2Tokenizer, GPT2Model

# Charger le tokenizer et le modèle GPT-2
gpt_tokenizer = GPT2Tokenizer.from_pretrained('gpt2')
gpt_model = GPT2Model.from_pretrained('gpt2')

# Encodage des documents
gpt_embeddings = []
for doc in preprocessed_corpus:
    inputs = gpt_tokenizer(doc, return_tensors='pt', padding=True, truncation=True, max_length=512)
    with torch.no_grad():
        outputs = gpt_model(**inputs)
    # Extraire l'embedding
    gpt_embeddings.append(outputs.last_hidden_state.mean(dim=1).squeeze().numpy())


## La différence entre les modèles trouvées et BERT

### BERT (Bidirectional Encoder Representations from Transformers)
Objectif principal : Apprentissage bidirectionnel pour une meilleure compréhension du contexte des mots.
Méthode d'entraînement :
Masked Language Model (MLM) : Masque certains mots dans la phrase et demande au modèle de prédire ces mots à partir du contexte.
Next Sentence Prediction (NSP) : Prédire si deux phrases se suivent logiquement.
Architecture : Encodeur uniquement.
Applications :
Compréhension de texte (classification, reconnaissance d’entités nommées).
Tâches nécessitant un contexte riche et bidirectionnel.

### GPT (Generative Pre-trained Transformer)
Objectif principal : Génération de texte basée sur un contexte donné.
Méthode d'entraînement :
Causal Language Model (CLM) : Prédiction du mot suivant dans une séquence.
Architecture : Décodeur uniquement (unidirectionnel).
Applications :
Tâches génératives comme la rédaction de texte, le résumé, ou la traduction.
Chatbots et assistants virtuels.
Limitation : N’examine que le contexte avant un mot donné, ce qui limite la compréhension globale dans certains cas.

### RoBERTa (A Robustly Optimized BERT Pretraining Approach)
Objectif principal : Améliorer les performances de BERT via des optimisations de l’entraînement.
Différences avec BERT :
Pas de Next Sentence Prediction (NSP) : Suppression de cette tâche, jugée inutile.
Corpus et temps d'entraînement étendus : Utilise plus de données et un entraînement plus long.
Masquage dynamique : Les mots masqués sont choisis dynamiquement à chaque époque, augmentant la robustesse.
Architecture : Identique à BERT (encodeur uniquement).
Applications :
Similaires à celles de BERT, mais avec des performances accrues dans des tâches comme la compréhension de texte.